In [ ]:
import numpy as np
import polars as pl
from datalit.dataloader import DataLoader

In [18]:

loader = DataLoader()

# Display available stations
print("Available stations:")
for station in loader.get_stations():
    print(f"  - {station}")

Available stations:
  - Eppelheimer Str. Querschnitt
  - Ernst-Walz-Brücke Querschnitt
  - Gaisbergstraße
  - Ernst-Walz-Brücke West - alt
  - Thedor-Heuss-Brücke Querschnitt
  - Plöck
  - Schlierbacher Landstraße
  - Bahnstadtpromenade
  - Kurfürstenanlage Querschnitt
  - Liebermannstraße
  - Mannheimer Straße
  - Berliner Straße Querschnitt
  - Ziegelhäuser Landstraße
  - Rohrbacher Straße Querschnitt
  - Hardtstraße


In [19]:
# Plot the difference between in and out channels
# This shows directional flow patterns (e.g., commute directions)

from plotly.subplots import make_subplots
import plotly.graph_objects as go

for station_name in loader.get_stations():
    # Get daily data for the full available range
    data = loader.get_data(station_name, sample_rate="1d")
    
    # Calculate the difference between in and out channels
    data = data.with_columns([
        (pl.col('channels_in') - pl.col('channels_out')).alias('daily_diff')
    ])
    
    # Get data for plotting
    dates = data.select('datetime').to_series().to_list()
    data_diff = data.select('daily_diff').to_series().to_numpy()
    data_all = data.select('channels_all').to_series().to_numpy()
    
    n = len(data_diff)
    
    # smoothing window: 24 days if available, otherwise a small window
    window = 24 if n >= 24 else max(3, n // 10)
    smoothed_diff = np.convolve(data_diff, np.ones(window) / window, mode='same')
    smoothed_all = np.convolve(data_all, np.ones(window) / window, mode='same')
    
    # Create interactive plot with Plotly using secondary y-axis
    fig = make_subplots(specs=[[{"secondary_y": True}]])
    
    # Raw data (diff) - on secondary axis (linear)
    fig.add_trace(go.Scatter(
        x=dates,
        y=data_diff,
        mode='lines',
        name='raw (daily diff)',
        line=dict(color='gray', width=0.5),
        opacity=0.25,
        hovertemplate='<b>Date:</b> %{x}<br><b>Daily Diff:</b> %{y}<extra></extra>'
    ), secondary_y=False)
    
    # Smoothed diff - on secondary axis (linear)
    fig.add_trace(go.Scatter(
        x=dates,
        y=smoothed_diff,
        mode='lines',
        name=f'{window}-day MA (daily diff [in-out])',
        line=dict(color='#1f77b4', width=2),
        hovertemplate='<b>Date:</b> %{x}<br><b>Smoothed Diff:</b> %{y:.1f}<extra></extra>'
    ), secondary_y=False)
    
    # Smoothed all channels - on primary axis (log scale)
    fig.add_trace(go.Scatter(
        x=dates,
        y=smoothed_all,
        mode='lines',
        name=f'{window}-day MA (all channels [in+out])',
        line=dict(color='#d62728', width=2),
        hovertemplate='<b>Date:</b> %{x}<br><b>Smoothed All:</b> %{y:.1f}<extra></extra>'
    ), secondary_y=True)
    
    fig.update_layout(
        title=f'Cycle Counter Data for {station_name}<br>from {dates[0]} to {dates[-1]}',
        xaxis_title='Date',
        height=500,
        width=1400,
        hovermode='x unified',
        legend=dict(x=0, y=1, orientation='h')
    )
    
    # Set y-axes titles
    fig.update_yaxes(title_text="Daily Difference (In - Out)", secondary_y=False)
    fig.update_yaxes(title_text="Total Channels (In + Out)", secondary_y=True)
    
    fig.show()